<a href="https://colab.research.google.com/github/DULAJBHAGYA/AI-IT-Path-Finder/blob/main/Dataset_preprocess.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import files
import json

# Upload your merged_profiles_all.json file
uploaded = files.upload()

# Load the JSON data
with open('merged_profiles_all.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

print(f"Loaded {len(data)} profiles")

Saving merged_profiles_all.json to merged_profiles_all.json
Loaded 3201 profiles


In [ ]:
import json

with open('merged_profiles_all.json', 'r', encoding='utf-8') as f:
    all_profiles = json.load(f)

# Check the types of the first few elements
for i, profile in enumerate(all_profiles[:10]):
    print(f"Index {i}: {type(profile)}")

# Find all non-dict entries
non_dict_indices = [i for i, profile in enumerate(all_profiles) if not isinstance(profile, dict)]
print(f"Non-dict entries found at indices: {non_dict_indices}")
if non_dict_indices:
    print("Example of non-dict entry:", all_profiles[non_dict_indices[0]])

Index 0: <class 'dict'>
Index 1: <class 'dict'>
Index 2: <class 'dict'>
Index 3: <class 'dict'>
Index 4: <class 'dict'>
Index 5: <class 'dict'>
Index 6: <class 'dict'>
Index 7: <class 'dict'>
Index 8: <class 'dict'>
Index 9: <class 'dict'>
Non-dict entries found at indices: [2200]
Example of non-dict entry: [{'name': 'Bradley Grimes', 'job_title': 'QA Engineer', 'contact': {'email': 'paul17@lopez-moore.com', 'phone': '001-142-387-4591', 'location': 'North Michael, Togo', 'linkedin': 'linkedin.com/in/richardhamilton', 'github': 'github.com/johnsonjamie', 'website': ''}, 'profile_summary': 'Experienced Business Analyst skilled in modern tools and technologies. Mouth step hope indeed front college rule traditional win body usually stock catch.', 'skills': [{'category': 'Languages', 'items': ['SQL', 'Python', 'Java']}, {'category': 'Frontend', 'items': ['HTML5', 'CSS3', 'JavaScript']}, {'category': 'Backend', 'items': ['Spring Boot', 'Django', 'Python']}], 'experience': [{'title': 'QA Engi

In [ ]:
all_profiles = [profile for profile in all_profiles if isinstance(profile, dict)]
print(f"Filtered profiles: {len(all_profiles)}")

Filtered profiles: 3200


In [ ]:
job_titles = [profile.get('job_title', 'Unknown') for profile in all_profiles]

In [ ]:
import pandas as pd

job_titles = [profile.get('job_title', 'Unknown') for profile in all_profiles]
job_title_counts = pd.Series(job_titles).value_counts()
print("Job Title Distribution:")
print(job_title_counts)

Job Title Distribution:
Business Analyst     1105
QA Engineer          1095
Software Engineer    1000
Name: count, dtype: int64


In [ ]:
def create_profile_hash(profile):
    name = profile.get('name', '').lower().strip()
    email = profile.get('contact', {}).get('email', '').lower().strip()
    return f"{name}|{email}"

seen_hashes = set()
unique_profiles = []
for profile in all_profiles:
    profile_hash = create_profile_hash(profile)
    if profile_hash not in seen_hashes:
        seen_hashes.add(profile_hash)
        unique_profiles.append(profile)

print(f"Removed {len(all_profiles) - len(unique_profiles)} duplicates")
print(f"Final dataset size: {len(unique_profiles)} profiles")

Removed 1000 duplicates
Final dataset size: 2200 profiles


In [ ]:
import json

def format_for_training(profile):
    text_parts = []
    if profile.get('name'):
        text_parts.append(f"Name: {profile['name']}")
    if profile.get('job_title'):
        text_parts.append(f"Title: {profile['job_title']}")
    contact = profile.get('contact', {})
    contact_info = ' | '.join(filter(None, [
        contact.get('email'),
        contact.get('phone'),
        contact.get('location'),
        contact.get('linkedin'),
        contact.get('github'),
        contact.get('website')
    ]))
    if contact_info:
        text_parts.append(f"Contact: {contact_info}")
    if profile.get('profile_summary'):
        text_parts.append(f"\nSummary:\n{profile['profile_summary']}")
    skills = profile.get('skills', [])
    if skills:
        skills_text = "\nSkills:\n"
        for skill_cat in skills:
            category = skill_cat.get('category', '')
            items = ', '.join(skill_cat.get('items', []))
            skills_text += f"- {category}: {items}\n"
        text_parts.append(skills_text)
    experience = profile.get('experience', [])
    if experience:
        exp_text = "\nWork Experience:\n"
        for exp in experience:
            exp_text += f"- {exp.get('title', '')}, {exp.get('company', '')} ({exp.get('duration', '')})\n"
            for resp in exp.get('responsibilities', []):
                exp_text += f"  - {resp}\n"
        text_parts.append(exp_text)
    return {
        "text": "\n".join(text_parts),
        "output": profile
    }

training_data = []
for profile in unique_profiles:
    try:
        training_example = format_for_training(profile)
        training_data.append(training_example)
    except Exception as e:
        print(f"Error formatting profile: {e}")

print(f"Created {len(training_data)} training examples")

Created 2200 training examples


In [ ]:
# Save cleaned JSON
with open('cleaned_profiles.json', 'w', encoding='utf-8') as f:
    json.dump(unique_profiles, f, indent=2)

# Save training dataset (JSONL format)
with open('training_dataset.jsonl', 'w', encoding='utf-8') as f:
    for example in training_data:
        f.write(json.dumps(example) + '\n')

print("Saved preprocessed data:")
print(f"- cleaned_profiles.json: {len(unique_profiles)} profiles")
print(f"- training_dataset.jsonl: {len(training_data)} training examples")

from google.colab import files
files.download('cleaned_profiles.json')
files.download('training_dataset.jsonl')

Saved preprocessed data:
- cleaned_profiles.json: 2200 profiles
- training_dataset.jsonl: 2200 training examples


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
import pandas as pd

job_titles = [profile.get('job_title', 'Unknown') for profile in unique_profiles]
job_title_counts = pd.Series(job_titles).value_counts()
print("Job Title Distribution:")
print(job_title_counts)

completeness_stats = {
    'Total Profiles': len(unique_profiles),
    'Profiles with Skills': sum(1 for p in unique_profiles if p.get('skills')),
    'Profiles with Experience': sum(1 for p in unique_profiles if p.get('experience')),
    'Profiles with Education': sum(1 for p in unique_profiles if p.get('education')),
    'Profiles with Summary': sum(1 for p in unique_profiles if p.get('profile_summary')),
}

print("\nData Completeness Report:")
for stat, count in completeness_stats.items():
    percentage = (count / len(unique_profiles)) * 100 if len(unique_profiles) > 0 else 0
    print(f"{stat}: {count} ({percentage:.1f}%)")

Job Title Distribution:
Software Engineer    1000
Business Analyst      605
QA Engineer           595
Name: count, dtype: int64

Data Completeness Report:
Total Profiles: 2200 (100.0%)
Profiles with Skills: 2200 (100.0%)
Profiles with Experience: 2200 (100.0%)
Profiles with Education: 2200 (100.0%)
Profiles with Summary: 2200 (100.0%)
